In [1]:
import numpy as np 
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import re
import string
from torch import nn
from torch import optim
from torch.utils.data import Dataset, DataLoader
import torch
import random
nltk.download('stopwords')
nltk.download('punkt')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Maxim\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Maxim\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [21]:
window_size = 5

epochs = 5
lr = 1e-2
batch_size = 16
embed_size = 300
path = 'trans.txt'
sw = stopwords.words('russian')

In [3]:
def preprocess_raw_text(path):
    with open(path, 'r', encoding='utf-8') as f:
        text = f.read().replace('\n', ' ')

        text = text.lower()
        
        text = text.replace('\xa0', ' ')

        text = re.sub(r'спикер (\d+|\?):', '', text)

        for punct in string.punctuation +'«»':
            text = text.replace(punct, ' ')

        while '  ' in text:
            text = text.replace('  ', ' ')

        raw_tokens = word_tokenize(text)
        
        tokens = []

        for token in raw_tokens:
            if token not in sw and token.isnumeric() == False:
                tokens.append(token)

        return tokens
        
tokens = preprocess_raw_text(path)

In [4]:
tokens

['кролик',
 'крош',
 'захотел',
 'сделать',
 'полезное',
 'своего',
 'домика',
 'решил',
 'смастерить',
 'скамееку',
 'сидеть',
 'друзьями',
 'вечерам',
 'делал',
 'её',
 'нескольких',
 'дней',
 'сделал',
 'покрасил',
 'рядом',
 'крошем',
 'жил',
 'ёжик',
 'который',
 'часто',
 'заходил',
 'нему',
 'гости',
 'здравствуй',
 'крош',
 'крош',
 'привет',
 'ёжик',
 'сделал',
 'понимаешь',
 'жду',
 'высохнет',
 'краска',
 'красивая',
 'получилась',
 'лавочка',
 'скорее',
 'понимаешь',
 'сесть',
 'неё',
 'краской',
 'красила',
 'быстросохнущей',
 'долгосохнущей',
 'неизвестно',
 'наверное',
 'высохла',
 'понимаешь',
 'высохла',
 'наверное',
 'это',
 'долгосохнущая',
 'краска',
 'крош',
 'любил',
 'ждать',
 'привык',
 'проводить',
 'время',
 'пользой',
 'принципе',
 'пока',
 'краска',
 'сохнет',
 'сделать',
 'ещё',
 'полезное',
 'понимаешь',
 'краска',
 'осталась',
 'тебе',
 'покрасить',
 'вроде',
 'это',
 'жаль',
 'давай',
 'тебе',
 'покрасим',
 'вспомнил',
 'барашу',
 'наверное',
 'нужно',
 

In [5]:
class SkipGramDataset(Dataset):
    def __init__(self, tokens, window_size=window_size):
        self.pairs = []
        for i in range(window_size, len(tokens) - window_size):
            target = tokens[i]
            
            context = tokens[i-window_size:i + window_size + 1]

            context.remove(target)

            for word in context:
                self.pairs.append((target, word))
    
    def __len__(self):
        return len(self.pairs)   

    def __getitem__(self, i):
        return self.pairs[i]

    
dataset = SkipGramDataset(tokens=tokens)

In [6]:
def converts(tokens):
    vocab = sorted(set(tokens))
    wtoi = {i : word for word, i in enumerate(vocab)}
    itow = {word : i for word, i in enumerate(vocab)}
    return wtoi, itow, vocab
wtoi, itow, vocab = converts(tokens)

In [7]:
X, y = [], []
for target, context in dataset:
    X.append(wtoi[target])
    y.append(wtoi[context])

X_train = torch.LongTensor(X)
y_train = torch.LongTensor(y)

In [8]:
class SkipGramModel(nn.Module):
    def __init__(self, vocab_size, embed_size ):
        super().__init__()
        self.embed = nn.Embedding(vocab_size, embed_size)
        self.linear = nn.Linear(embed_size, vocab_size)
        self.softmax = nn.Softmax()

    def forward(self, x):
        return self.softmax(self.linear(self.embed(x)))
    
    def K_nearest(self, x, k):
        x_vec = torch.tensor(wtoi[x], dtype=torch.long)
        all_vecs = self.embed.weight.detach()
        
        sims = nn.functional.cosine_similarity(x_vec.unsqueeze(0), all_vecs, dim=1)
        
        topk = torch.topk(sims, k+1)
        indices = topk.indices.tolist()
        scores = topk.values.tolist()
        

        result = [(itow[i], s) for i, s in zip(indices, scores) if i != x]
        return result[:k]

In [9]:
model = SkipGramModel(len(vocab), embed_size=embed_size)

loss_func = nn.CrossEntropyLoss()
opt = optim.Adam(model.parameters(), lr=lr)

In [10]:
def train(model, loss_func, opt):
    for epoch in range(epochs):
        total_loss = 0
        for i in range(0, len(X), batch_size):

            x = X_train[i:i+batch_size]
            y = y_train[i:i+batch_size]

            opt.zero_grad()
            y_pred = model(x)
            loss = loss_func(y_pred, y.view(-1))
            loss.backward()
            opt.step()
            
            total_loss += loss.item() / batch_size
        print(f'Epoch num: {epoch+1}, loss value: {total_loss:.3f}')

In [11]:
train(model,loss_func,opt)

c:\Users\Maxim\porjs\word2vec\.venv\Lib\site-packages\torch\nn\modules\module.py:1773: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  return self._call_impl(*args, **kwargs)


Epoch num: 1, loss value: 417.441
Epoch num: 2, loss value: 414.502
Epoch num: 3, loss value: 413.096
Epoch num: 4, loss value: 412.837
Epoch num: 5, loss value: 412.725


In [12]:
model.K_nearest('крош', 5)

[('надеялся', 0.22066408395767212),
 ('хлопнула', 0.193851500749588),
 ('спи', 0.17391185462474823),
 ('ура', 0.17332887649536133),
 ('делся', 0.170402392745018)]

In [13]:
def get_tokens_freq(tokens):
    vocab_freq = {}
    for token in tokens:
        if token not in vocab_freq:
            vocab_freq[token] = 1
        else:
            vocab_freq[token] += 1

    return {k: v/len(tokens) for k, v in sorted(vocab_freq.items(), key=lambda item: item[1], reverse=True)}


## Subsampling


In [14]:
def flag_to_drop(freq) -> bool:
    p = max(1 - np.sqrt(1e-3/freq), 0)
    return random.random() <= p

In [15]:
def subsampling(tokens):
    vocab_freq = get_tokens_freq(tokens)
    subsampled_tokens = []
    for token in tokens:
        if not flag_to_drop(vocab_freq[token]):
            subsampled_tokens.append(token)
    return subsampled_tokens

In [16]:
tokens = subsampling(tokens)
wtoi, itow, vocab = converts(tokens)
dataset = SkipGramDataset(tokens=tokens)
X, y = [], []
for target, context in dataset:
    X.append(wtoi[target])
    y.append(wtoi[context])

X_train = torch.LongTensor(X)
y_train = torch.LongTensor(y)

model = SkipGramModel(len(vocab), embed_size=embed_size)

loss_func = nn.CrossEntropyLoss()
opt = optim.Adam(model.parameters(), lr=lr)
train(model, loss_func, opt)

Epoch num: 1, loss value: 359.057
Epoch num: 2, loss value: 356.204
Epoch num: 3, loss value: 354.572
Epoch num: 4, loss value: 354.295
Epoch num: 5, loss value: 354.240


In [17]:
model.K_nearest('стены', 5)

[('краской', 0.2022850513458252),
 ('вверх', 0.17448820173740387),
 ('пять', 0.17252139747142792),
 ('художественное', 0.1688108891248703),
 ('использовать', 0.15680217742919922)]

## Negative Sampling

составим датасет, включающий негативные примеры. решим задачу бинарной классификации

In [18]:
class SkipGramDataset(Dataset):
    def __init__(self, tokens, window_size=window_size):
        self.pairs = []
        for i in range(window_size, len(tokens) - window_size):
            target = tokens[i]
            
            context = tokens[i-window_size:i + window_size + 1]

            context.remove(target)

            for word in context:
                self.pairs.append((target, word))
    
    def __len__(self):
        return len(self.pairs)   

    def __getitem__(self, i):
        return self.pairs[i]

In [43]:
str(np.random.choice(vocab))

'бегает'

In [115]:
class NegativeSamplingDataset(Dataset):
    def __init__(self, tokens, window_size, negatives_number=5):
        self.data = []
        self.vocab = sorted(set(tokens))
        for i in range(window_size, len(tokens) - window_size):
            target = tokens[i]
            context = tokens[i-window_size:i + window_size + 1]
            context.remove(target)
            for word in context:
                self.data.append([target, word,1])    
                for _ in range(negatives_number):
                    self.data.append([target, str(np.random.choice(self.vocab)), 0])   
            
    def __len__(self):
        return len(self.data)   

    def __getitem__(self, i):
        return self.data[i]
dataset = NegativeSamplingDataset(tokens, window_size)

In [83]:
dl = DataLoader(dataset, 216, shuffle=True, collate_fn = lambda b: b)

In [114]:
for i in dl:
    print(i)
    

[['глупый', 'книге', 0], ['пусть', 'девушки', 0], ['культурный', 'наглее', 1], ['сердечные', 'двигатель', 0], ['думаешь', 'земли', 0], ['прислушайтесь', 'лета', 0], ['приготовления', 'радостном', 0], ['храпит', 'берлога', 1], ['кроша', 'бараша', 1], ['приятно', 'хм', 0], ['наглее', 'предельно', 0], ['писать', 'вырви', 1], ['пользы', 'мешать', 0], ['убираться', 'рассказывал', 0], ['маленьких', 'зря', 0], ['всё', 'разных', 0], ['понимаю', 'энергия', 0], ['просто', 'вкуса', 0], ['урожай', 'гантели', 0], ['скоро', 'везде', 0], ['смысл', 'сладкое', 0], ['друг', 'ровно', 0], ['переживай', 'ваши', 0], ['книгу', 'нюшей', 0], ['прыгал', 'часов', 0], ['голову', 'перестань', 0], ['особенно', 'забудет', 0], ['одиночества', 'острова', 0], ['часто', 'жизнь', 0], ['делалась', 'девушки', 0], ['около', 'поведение', 0], ['бегемот', 'первым', 0], ['культурный', 'ушли', 0], ['приятно', 'чай', 0], ['да…', 'ай', 0], ['конце', 'вами', 0], ['надолго', 'приступаем', 0], ['урожай', 'такая', 0], ['чаю', 'попробу

In [ ]:
class SGNGModel(nn.Module):
    def __init__(self, vocab_size, embed_size):
        super().__init__()
        self.vocab_size = vocab_size
        self.target_emb = nn.Embedding(vocab_size, embed_size)
        self.context_emb = nn.Embedding(vocab_size, embed_size) # можно представить, что в последнем слое хранятся ембеддинги тех же слов, что и в target_emb, но в качестве контекста, а не таргета
        self.log_sigmoid = nn.LogSigmoid()
    
    def forward(self, target, conтвыфtext, ):
        

In [ ]:
class NegativeSamplingDataset(Dataset):
    def __init__(self, tokens, window_size, negatives_number=5):
        self.x, self.y = [], []
        self.vocab = sorted(set(tokens))
        for i in range(window_size, len(tokens) - window_size):
            target = tokens[i]
                
            context = tokens[i-window_size:i + window_size + 1]

            context.remove(target)
            vocab_without_context_tokens = [i for i in self.vocab if i not in context]

            for word in context:
                self.x.append((target, word))
                self.y.append(1)
                negatives = np.random.choice(vocab_without_context_tokens, negatives_number)
                for word in negatives:
                    self.x.append((target, str(word)))
                    self.y.append(0)
   
            
    def __len__(self):
        return len(self.y)   

    def __getitem__(self, i):
        return self.x[i], self.y[i]
        
dataset = NegativeSamplingDataset(tokens, window_size)